In [1]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.naive_bayes import MultinomialNB
from sklearn.decomposition import NMF, LatentDirichletAllocation
from sklearn.decomposition import TruncatedSVD
from sklearn.feature_extraction.text import CountVectorizer 
from sklearn.feature_extraction import text
from sklearn.feature_extraction.text import TfidfVectorizer  
from sklearn import metrics
from sklearn.metrics import accuracy_score, precision_score,recall_score,matthews_corrcoef,cohen_kappa_score
from sklearn.preprocessing import MinMaxScaler
import re
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
import time as time

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/bharath/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [2]:
categories = ['alt.atheism', 'talk.religion.misc', 'comp.graphics', 'sci.space']
newsgroups_train = fetch_20newsgroups(subset='train',categories=categories)

In [3]:
newsgroups_train

{'data': ["From: rych@festival.ed.ac.uk (R Hawkes)\nSubject: 3DS: Where did all the texture rules go?\nLines: 21\n\nHi,\n\nI've noticed that if you only save a model (with all your mapping planes\npositioned carefully) to a .3DS file that when you reload it after restarting\n3DS, they are given a default position and orientation.  But if you save\nto a .PRJ file their positions/orientation are preserved.  Does anyone\nknow why this information is not stored in the .3DS file?  Nothing is\nexplicitly said in the manual about saving texture rules in the .PRJ file. \nI'd like to be able to read the texture rule information, does anyone have \nthe format for the .PRJ file?\n\nIs the .CEL file format available from somewhere?\n\nRych\n\n======================================================================\nRycharde Hawkes\t\t\t\temail: rych@festival.ed.ac.uk\nVirtual Environment Laboratory\nDept. of Psychology\t\t\tTel  : +44 31 650 3426\nUniv. of Edinburgh\t\t\tFax  : +44 31 667 0150\n====

In [4]:
newsgroups_train.data

["From: rych@festival.ed.ac.uk (R Hawkes)\nSubject: 3DS: Where did all the texture rules go?\nLines: 21\n\nHi,\n\nI've noticed that if you only save a model (with all your mapping planes\npositioned carefully) to a .3DS file that when you reload it after restarting\n3DS, they are given a default position and orientation.  But if you save\nto a .PRJ file their positions/orientation are preserved.  Does anyone\nknow why this information is not stored in the .3DS file?  Nothing is\nexplicitly said in the manual about saving texture rules in the .PRJ file. \nI'd like to be able to read the texture rule information, does anyone have \nthe format for the .PRJ file?\n\nIs the .CEL file format available from somewhere?\n\nRych\n\n======================================================================\nRycharde Hawkes\t\t\t\temail: rych@festival.ed.ac.uk\nVirtual Environment Laboratory\nDept. of Psychology\t\t\tTel  : +44 31 650 3426\nUniv. of Edinburgh\t\t\tFax  : +44 31 667 0150\n=============

In [5]:
s = newsgroups_train.data[0]

In [6]:
newsgroups_train.data[0]

"From: rych@festival.ed.ac.uk (R Hawkes)\nSubject: 3DS: Where did all the texture rules go?\nLines: 21\n\nHi,\n\nI've noticed that if you only save a model (with all your mapping planes\npositioned carefully) to a .3DS file that when you reload it after restarting\n3DS, they are given a default position and orientation.  But if you save\nto a .PRJ file their positions/orientation are preserved.  Does anyone\nknow why this information is not stored in the .3DS file?  Nothing is\nexplicitly said in the manual about saving texture rules in the .PRJ file. \nI'd like to be able to read the texture rule information, does anyone have \nthe format for the .PRJ file?\n\nIs the .CEL file format available from somewhere?\n\nRych\n\n======================================================================\nRycharde Hawkes\t\t\t\temail: rych@festival.ed.ac.uk\nVirtual Environment Laboratory\nDept. of Psychology\t\t\tTel  : +44 31 650 3426\nUniv. of Edinburgh\t\t\tFax  : +44 31 667 0150\n==============

In [7]:
n = len(newsgroups_train.data)
corpus = []
for i in range(n):
    doing_prepro = re.sub('[^a-zA-Z]', ' ', newsgroups_train.data[i])
    doing_prepro = doing_prepro.lower()
    doing_prepro = doing_prepro.split()
    ps = PorterStemmer()
    doing_prepro = [ps.stem(word) for word in doing_prepro if not word in set(stopwords.words('english'))]
    
    
    doing_prepro = ' '.join(doing_prepro)
    corpus.append(doing_prepro)

In [8]:
vectorizer = CountVectorizer()
vectors = vectorizer.fit_transform(corpus)
vectors.shape

(2034, 21051)

In [9]:
corpus

['rych festiv ed ac uk r hawk subject ds textur rule go line hi notic save model map plane posit care ds file reload restart ds given default posit orient save prj file posit orient preserv anyon know inform store ds file noth explicitli said manual save textur rule prj file like abl read textur rule inform anyon format prj file cel file format avail somewher rych rychard hawk email rych festiv ed ac uk virtual environ laboratori dept psycholog tel univ edinburgh fax',
 'subject biblic back koresh tape cite enclos kmcvay oneb almanac bc ca ken mcvay organ old frog almanac line articl apr utarlg uta edu b zaw utarlg uta edu stephen write seem koresh yet anoth messeng got kill messag carri say noth seem bar evid contrari koresh simpli anoth derang fanat thought neccessari take whole bunch folk children satisfi delusion mania jim jone circa mean time sure learn lot evil corrupt surpris thing gotten rotten nope fruitcak like koresh demonstr evil corrupt centuri old frog almanac salut old f

In [10]:
print('ar')

ar


In [11]:
len(corpus)

2034

In [12]:
newsgroups_train = fetch_20newsgroups(subset='train', remove=('headers', 'footers', 'quotes'),categories=categories) 
corpus_train = []
n=len(newsgroups_train.data)

for i in range(n):
    doing_prepro = re.sub('[^a-zA-Z]', ' ', newsgroups_train.data[i])
    doing_prepro = doing_prepro.lower()
    doing_prepro = doing_prepro.split()
    ps = PorterStemmer()
    doing_prepro = [ps.stem(word) for word in doing_prepro if not word in set(stopwords.words('english'))]
    
    
    doing_prepro = ' '.join(doing_prepro)
    corpus_train.append(doing_prepro)

In [13]:
len(corpus_train)

2034

In [14]:
newsgroups_test = fetch_20newsgroups(subset='test', remove=('headers', 'footers', 'quotes'),categories=categories) 
n = len(newsgroups_test.data)
print(n)
corpus_test = []
for i in range(n):
    doing_prepro = re.sub('[^a-zA-Z]', ' ', newsgroups_test.data[i])
    doing_prepro = doing_prepro.lower()
    doing_prepro = doing_prepro.split()
    ps = PorterStemmer()
    doing_prepro = [ps.stem(word) for word in doing_prepro if not word in set(stopwords.words('english'))]
    
    
    doing_prepro = ' '.join(doing_prepro)
    corpus_test.append(doing_prepro)

1353


In [15]:
len(corpus_test)

1353

In [16]:
tfidf_vectorizer = TfidfVectorizer(max_df=0.5, max_features=10000,
                             min_df=2, stop_words='english',
                             use_idf=True)

vectors = tfidf_vectorizer.fit_transform(corpus_train)
no_topics = 50

start1 = time.time()
lda_model = LatentDirichletAllocation(n_components=no_topics, random_state=0)
lda_train = lda_model.fit_transform(vectors)
end1 = time.time()

clf = MultinomialNB(alpha=.01)
clf.fit(lda_train, newsgroups_train.target)

newsgroups_test = fetch_20newsgroups(subset='test', remove=('headers', 'footers', 'quotes'),categories=categories) 
vectors_test = tfidf_vectorizer.transform(corpus_test)

start2 = time.time()
lda_test = lda_model.transform(vectors_test)
end2 = time.time()

pred = clf.predict(lda_test)

print("F1 Score:"+str(metrics.f1_score(newsgroups_test.target, pred, average='macro')))
print("Accuracy:"+str(accuracy_score(newsgroups_test.target,pred)))
print("Precision:"+str(precision_score(newsgroups_test.target,pred, average='macro')))
print("Recall:"+str(recall_score(newsgroups_test.target,pred, average='macro')))
print("Time:"+str((end1-start1)+(end2-start2)))
print("Matthew's correlation coefficient:"+str(matthews_corrcoef(newsgroups_test.target,pred)))
print("Cohen Kappa Score:"+str(cohen_kappa_score(newsgroups_test.target,pred)))

F1 Score:0.27903487371611724
Accuracy:0.3991130820399113
Precision:0.6166941499235773
Recall:0.3481731053085879
Time:9.489670753479004
Matthew's correlation coefficient:0.18177863119954274
Cohen Kappa Score:0.15556492120190424


In [17]:
count_vectorizer = CountVectorizer(max_df=0.5, max_features=10000,
                             min_df=2, stop_words='english')

vectors = count_vectorizer.fit_transform(corpus_train)
no_topics = 50

start1 = time.time()
lda_model = LatentDirichletAllocation(n_components=no_topics, random_state=0)
lda_train = lda_model.fit_transform(vectors)
end1 = time.time()

clf = MultinomialNB(alpha=.01)
clf.fit(lda_train, newsgroups_train.target)
 
vectors_test = count_vectorizer.transform(corpus_test)
start2 = time.time()
lda_test = lda_model.transform(vectors_test)
end2 = time.time()
pred = clf.predict(lda_test)

print("F1 Score:"+str(metrics.f1_score(newsgroups_test.target, pred, average='macro')))
print("Accuracy:"+str(accuracy_score(newsgroups_test.target,pred)))
print("Precision:"+str(precision_score(newsgroups_test.target,pred, average='macro')))
print("Recall:"+str(recall_score(newsgroups_test.target,pred, average='macro')))
print("Time:"+str((end1-start1)+(end2-start2)))
print("Matthew's correlation coefficient:"+str(matthews_corrcoef(newsgroups_test.target,pred)))
print("Cohen Kappa Score:"+str(cohen_kappa_score(newsgroups_test.target,pred)))

F1 Score:0.6500153465707494
Accuracy:0.6999260901699926
Precision:0.6895795144827652
Recall:0.6589587454161254
Time:19.67633628845215
Matthew's correlation coefficient:0.5983529343026575
Cohen Kappa Score:0.5909689986552233


In [18]:
tfidf_vectorizer = TfidfVectorizer(max_df=0.5, max_features=10000,
                             min_df=2, stop_words='english',
                             use_idf=True)

vectors = tfidf_vectorizer.fit_transform(corpus_train)
no_topics = 50

start1 = time.time()
nmf_model = NMF(n_components=no_topics, init = "nndsvd")
nmf_train = nmf_model.fit_transform(vectors)
end1 = time.time()

clf = MultinomialNB(alpha=.01)
clf.fit(nmf_train, newsgroups_train.target)

newsgroups_test = fetch_20newsgroups(subset='test', remove=('headers', 'footers', 'quotes'),categories=categories) 
vectors_test = tfidf_vectorizer.transform(corpus_test)

start2 = time.time()
nmf_test = nmf_model.transform(vectors_test)
end2 = time.time()

pred = clf.predict(nmf_test)

print("F1 Score:"+str(metrics.f1_score(newsgroups_test.target, pred, average='macro')))
print("Accuracy:"+str(accuracy_score(newsgroups_test.target,pred)))
print("Precision:"+str(precision_score(newsgroups_test.target,pred, average='macro')))
print("Recall:"+str(recall_score(newsgroups_test.target,pred, average='macro')))
print("Time:"+str((end1-start1)+(end2-start2)))
print("Matthew's correlation coefficient:"+str(matthews_corrcoef(newsgroups_test.target,pred)))
print("Cohen Kappa Score:"+str(cohen_kappa_score(newsgroups_test.target,pred)))

F1 Score:0.5198834065458906
Accuracy:0.6348854397634885
Precision:0.7447995844734975
Recall:0.571612724718398
Time:10.393465280532837
Matthew's correlation coefficient:0.5278289451076082
Cohen Kappa Score:0.49317696516748966


In [19]:
count_vectorizer = CountVectorizer(max_df=0.5, max_features=10000,
                             min_df=2, stop_words='english')

vectors = count_vectorizer.fit_transform(corpus_train)
no_topics = 50

start1 = time.time()
nmf_model = NMF(n_components=no_topics, init = "nndsvd")
nmf_train = nmf_model.fit_transform(vectors)
end1 = time.time()

clf = MultinomialNB(alpha=.01)
clf.fit(nmf_train, newsgroups_train.target)

vectors_test = count_vectorizer.transform(corpus_test)

start2 = time.time()
nmf_test = nmf_model.transform(vectors_test)
end2 = time.time()

pred = clf.predict(nmf_test)

print("F1 Score:"+str(metrics.f1_score(newsgroups_test.target, pred, average='macro')))
print("Accuracy:"+str(accuracy_score(newsgroups_test.target,pred)))
print("Precision:"+str(precision_score(newsgroups_test.target,pred, average='macro')))
print("Recall:"+str(recall_score(newsgroups_test.target,pred, average='macro')))
print("Time:"+str((end1-start1)+(end2-start2)))
print("Matthew's correlation coefficient:"+str(matthews_corrcoef(newsgroups_test.target,pred)))
print("Cohen Kappa Score:"+str(cohen_kappa_score(newsgroups_test.target,pred)))

F1 Score:0.5598193001889163
Accuracy:0.631189948263119
Precision:0.6559907616892912
Recall:0.5807808287462316
Time:10.648354291915894
Matthew's correlation coefficient:0.510756812299417
Cohen Kappa Score:0.49118701701552325


In [20]:
tfidf_vectorizer = TfidfVectorizer(max_df=0.5, max_features=10000,
                             min_df=2, stop_words='english',
                             use_idf=True)

vectors = tfidf_vectorizer.fit_transform(corpus_train)
no_topics = 50

start1 = time.time()
lsa_model = TruncatedSVD(n_components=no_topics,
                         algorithm='randomized',
                         n_iter=50)
lsa_train = lsa_model.fit_transform(vectors)

scaler = MinMaxScaler()        # Scale features to make them positive
lsa_train = scaler.fit_transform(lsa_train)
end1 = time.time()

clf = MultinomialNB(alpha=.01)
clf.fit(lsa_train, newsgroups_train.target)

vectors_test = tfidf_vectorizer.transform(corpus_test)

start2 = time.time()
lsa_test = lsa_model.transform(vectors_test)
lsa_test = scaler.transform(lsa_test)
end2 = time.time()

pred = clf.predict(lsa_test)

print("F1 Score:"+str(metrics.f1_score(newsgroups_test.target, pred, average='macro')))
print("Accuracy:"+str(accuracy_score(newsgroups_test.target,pred)))
print("Precision:"+str(precision_score(newsgroups_test.target,pred, average='macro')))
print("Recall:"+str(recall_score(newsgroups_test.target,pred, average='macro')))
print("Time:"+str((end1-start1)+(end2-start2)))
print("Matthew's correlation coefficient:"+str(matthews_corrcoef(newsgroups_test.target,pred)))
print("Cohen Kappa Score:"+str(cohen_kappa_score(newsgroups_test.target,pred)))

F1 Score:0.3348507168101021
Accuracy:0.5055432372505543
Precision:0.5379186931335118
Recall:0.4367307742103623
Time:1.3954658508300781
Matthew's correlation coefficient:0.3874077783706126
Cohen Kappa Score:0.30354430613497974


/home/bharath/anaconda3/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/bharath/anaconda3/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


In [21]:
count_vectorizer = CountVectorizer(max_df=0.5, max_features=10000,
                             min_df=2, stop_words='english')

vectors = count_vectorizer.fit_transform(corpus_train)
no_topics = 50

start1 = time.time()
lsa_model = TruncatedSVD(n_components=no_topics,
                         algorithm='randomized',
                         n_iter=50)
lsa_train = lsa_model.fit_transform(vectors)

scaler = MinMaxScaler()         # Scale features to make them positive
lsa_train = scaler.fit_transform(lsa_train)
end1 = time.time()

clf = MultinomialNB(alpha=.01)
clf.fit(lsa_train, newsgroups_train.target)

vectors_test = count_vectorizer.transform(corpus_test)

start2 = time.time()
lsa_test = lsa_model.transform(vectors_test)
lsa_test = scaler.transform(lsa_test)
end2 = time.time()

pred = clf.predict(lsa_test)

print("F1 Score:"+str(metrics.f1_score(newsgroups_test.target, pred, average='macro')))
print("Accuracy:"+str(accuracy_score(newsgroups_test.target,pred)))
print("Precision:"+str(precision_score(newsgroups_test.target,pred, average='macro')))
print("Recall:"+str(recall_score(newsgroups_test.target,pred, average='macro')))
print("Time:"+str((end1-start1)+(end2-start2)))
print("Matthew's correlation coefficient:"+str(matthews_corrcoef(newsgroups_test.target,pred)))
print("Cohen Kappa Score:"+str(cohen_kappa_score(newsgroups_test.target,pred)))

F1 Score:0.1340621791311081
Accuracy:0.30155210643015523
Precision:0.24360692771084339
Recall:0.25902189657197294
Time:1.378647804260254
Matthew's correlation coefficient:0.06346616638254017
Cohen Kappa Score:0.014693461729338941


/home/bharath/anaconda3/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/bharath/anaconda3/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
